# TIEGCM


The kamodofied TIEGCM requires `netCDF4` (and numpy, scipy, and pandas, but those are required by kamodo)

    pip install netCDF4

In [1]:
#import block
%load_ext autoreload
%autoreload 2
from plotly.offline import init_notebook_mode, iplot, plot
init_notebook_mode(connected = True)
import numpy as np
from kamodo.readers.tiegcm_4D import MODEL, model_varnames
from kamodo.readers.reader_kplots import plot2D
from time import perf_counter
t0=perf_counter()
reader = MODEL()
print(perf_counter()-t0, 's')

KAMODO IMPORTED!
0.007897299999999774 s


In [2]:
#print possible variable names for given model
print('Standardized variables:\n---------------------------')
for key in model_varnames.keys():
    print(model_varnames[key][0]+':', model_varnames[key][1:])

Standardized variables:
---------------------------
H_ilev: ['variable description', 0, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], 'cm']
T_n: ['variable description', 1, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], 'K']
psi_O2: ['variable description', 2, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_O: ['variable description', 3, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_N2: ['variable description', 4, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_He: ['variable description', 5, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_NO: ['variable description', 6, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_N4S: ['variable description', 7, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
psi_N2D: ['variable description', 8, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], '']
T_e: ['variable description', 9, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], 'K']
T_i: ['variable description', 10, 'GDZ', 'sph', ['time', 'lon', 'lat', 'ilev'], 'K']
N_O2

In [3]:
#set filename, run_name, desired variable list, and whether gridded interpolators are desired
#filename = 'C:/Users/rringuet/Kamodo_WinDev1/TIEGCM/Data/s002.nc'
filename = 'C:/Users/rringuet/Kamodo_WinDev1/TIEGCM/Data/s322.nc'  #doesn't have any 3D variables, including TEC
run_name = "TIEGCM_Eunsol_Kim_021320_IT_2"
var_list, gridded_int = ['rho','H_mag','TEC'], False  # 
var_3D = 'TEC'  #for testing of expected plot error in last cell, should be a 3D variable name (if possible)

In [4]:
#get desired variables from model output
tic = perf_counter()
kamodo_object = reader(filename, runname=run_name)  #load all variables
#kamodo_object = reader(filename, variables_requested=var_list, runname=run_name, gridded_int=gridded_int)  #load specified variables with gridded interpolators
print(perf_counter()-tic, 's for ', len(kamodo_object.variables.keys()), ' variables')

c:\users\rringuet\kamodo_windev1\kamodo-master\kamodo\readers\tiegcm_4D.py:254: UserWarning:

cannot be safely cast to variable data type



All values at max milev are 1e+36 for H_mag. Slicing off top array.
All values at max milev are 1e+36 for H_mag. Slicing off top array.
All values at max milev are 1e+36 for H_mag. Slicing off top array.
3.4858105 s for  24  variables


In [5]:
#show functionalized variables in kamodo object
kamodo_object

{T_n(xvec): <function define_4d_interpolator.<locals>.interpolator at 0x000001B8ED88BC18>, T_n: <function define_4d_interpolator.<locals>.interpolator at 0x000001B8ED88BC18>, T_n_ijk(time, lon, lat, ilev): <function gridify.<locals>.decorator_gridify.<locals>.wrapped at 0x000001B896F6D8B8>, T_n_ijk: <function gridify.<locals>.decorator_gridify.<locals>.wrapped at 0x000001B896F6D8B8>, u_n(xvec): <function define_4d_interpolator.<locals>.interpolator at 0x000001B896F6DAF8>, u_n: <function define_4d_interpolator.<locals>.interpolator at 0x000001B896F6DAF8>, u_n_ijk(time, lon, lat, ilev): <function gridify.<locals>.decorator_gridify.<locals>.wrapped at 0x000001B896F5A3A8>, u_n_ijk: <function gridify.<locals>.decorator_gridify.<locals>.wrapped at 0x000001B896F5A3A8>, v_n(xvec): <function define_4d_interpolator.<locals>.interpolator at 0x000001B896F5A678>, v_n: <function define_4d_interpolator.<locals>.interpolator at 0x000001B896F5A678>, v_n_ijk(time, lon, lat, ilev): <function gridify.<loc

In [6]:
#set variables to be plotted
if gridded_int:  #set list of variables to check plots, list should include at least one 3D and at least one 4D variable
    plot_list = list(np.ravel([[var, var+'_ijk'] for var in var_list]))
else:
    plot_list = var_list
print(plot_list)

#pick plotting values and ranges
lonval, lonarr = 60., np.linspace(-180.,180.,200)
latval, latarr = -20., np.linspace(-90.,90.,100)
min_time, max_time = kamodo_object._time.min(), kamodo_object._time.max()
timeval, timearr = np.mean([min_time, max_time]), np.linspace(min_time,max_time,50)

['rho', 'H_mag', 'TEC']


In [7]:
#show variable coordinate dependencies (especially for non-gridded variables)
for key in kamodo_object.variables.keys(): print(key, kamodo_object.variables[key]['xvec'])

T_n {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
T_n_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
u_n {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
u_n_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
v_n {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
v_n_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_O2 {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_O2_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_O {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_O_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_N2 {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_N2_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_He {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
psi_He_ijk {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev': 'm/m'}
rho {'time': 'hr', 'lon': 'deg', 'lat': 'deg', 'ilev1': 'm/m'}
rho_ijk {'time': 'h

In [8]:
#show documentation for 2D plotting function
help(plot2D)

Help on function plot2D in module kamodo.readers.reader_kplots:

plot2D(kamodo_object, varname, plottype, t, lon, lat, h=-1)
    Use Kamodo's native plotting to generate 2D plot.
    Possible plot types are LonLat, LatH, LonH, TimeLat, TimeLon, and TimeH.
    If the variable depends on 4 dimensions, h should be given.
    If a LonLat plot is requested, then the function expects a single value
        (integer, float, float32, or float64) for t and h (if h is given).
        In this case, lon and lat should be 1D arrays or flat lists.
    If the variable depends on height, then a value or array should be given for h.



In [9]:
#generate each possible type of 2D plot for each variable in plot_list
for plot_var in plot_list:
    if plot_var not in kamodo_object.variables.keys(): continue
    print('---------------------------------------------------------------')
    print(f'--------------  Plots for {plot_var}  -----------------------')
    print('---------------------------------------------------------------')
    if len(list(kamodo_object.variables[plot_var]['xvec'].keys()))==4:  #if height depedent
        #get acceptable range for height based on variable chosen
        if 'milev' in kamodo_object.variables[plot_var]['xvec'].keys():
            hmin, hmax, hval = kamodo_object._milev.min(), kamodo_object._milev.max(), np.mean([kamodo_object._milev.max(),kamodo_object._milev.min()])
        elif 'ilev' in kamodo_object.variables[plot_var]['xvec'].keys():
            hmin, hmax, hval = kamodo_object._ilev.min(), kamodo_object._ilev.max(), np.mean([kamodo_object._ilev.max(),kamodo_object._ilev.min()])
        elif 'ilev1' in kamodo_object.variables[plot_var]['xvec'].keys():
            hmin, hmax, hval = kamodo_object._ilev1.min(), kamodo_object._ilev1.max(), np.mean([kamodo_object._ilev1.max(),kamodo_object._ilev1.min()])
        elif 'height' in kamodo_object.variables[plot_var]['xvec'].keys():
            hmin, hmax, hval = kamodo_object._height.min(), kamodo_object._height.max(), np.mean([kamodo_object._height.max(),kamodo_object._height.min()])
        height_arr = np.linspace(hmin, hmax, 150)
        print(plot_var, hmax, hmin)

        #make 2D plots for variable
        iplot(plot2D(kamodo_object, plot_var,'LonLat',timeval,lonarr,latarr,hval))
        iplot(plot2D(kamodo_object, plot_var,'TimeLat',timearr,lonval,latarr,hval))
        iplot(plot2D(kamodo_object, plot_var,'TimeLon',timearr,lonarr,latval,hval))
        iplot(plot2D(kamodo_object, plot_var,'LonH',timeval,lonarr,latval,height_arr))
        iplot(plot2D(kamodo_object, plot_var,'LatH',timeval,lonval,latarr,height_arr))
        iplot(plot2D(kamodo_object, plot_var,'TimeH',timearr,lonval,latval,height_arr))
    else:  #only height-independent plots
        #make 2D plots for variable
        iplot(plot2D(kamodo_object, plot_var,'LonLat',timeval,lonarr,latarr))
        iplot(plot2D(kamodo_object, plot_var,'TimeLat',timearr,lonval,latarr))
        iplot(plot2D(kamodo_object, plot_var,'TimeLon',timearr,lonarr,latval))  

---------------------------------------------------------------
--------------  Plots for rho  -----------------------
---------------------------------------------------------------
rho 7.0 -7.0
Time slice at 12.000 hrs. Pressure level slice at 0.0.


Longitude slice at 60.000 deg. Pressure level slice at 0.0.


Latitude slice at -20.000 deg. Pressure level slice at 0.0.


Time slice at 12.000 hrs. Latitude slice at -20.000 deg. 


Time slice at 12.000 hrs. Longitude slice at 60.000 deg. 


...

Longitude slice at 60.000 deg. Pressure level slice at -1.5.


Latitude slice at -20.000 deg. Pressure level slice at -1.5.


Time slice at 12.000 hrs. Latitude slice at -20.000 deg. 


Time slice at 12.000 hrs. Longitude slice at 60.000 deg. 


Longitude slice at 60.000 deg. Latitude slice at -20.000 deg. 


In [10]:
#Show proper errors when user tries to plot a time+2D variable against height
if var_3D in kamodo_object.variables.keys():
    try:
        iplot(plot2D(kamodo_object, var_3D,'LonH',timeval,lonarr,latval,height_arr))
    except AttributeError as e:
        print(e)
    try:
        iplot(plot2D(kamodo_object, var_3D,'LatH',timeval,lonval,latarr,height_arr))
    except AttributeError as e:
        print(e)   
    try:
        iplot(plot2D(kamodo_object, var_3D,'TimeH',timearr,lonval,latval,height_arr))
    except AttributeError as e:
        print(e)   
else:
    print('No 3D variable given.')

No 3D variable given.


In [11]:
kamodo_object._time.min(), kamodo_object._time.max(), kamodo_object._time[0], kamodo_object._time[-1]

(0.0, 24.0, 0.0, 24.0)

In [12]:
kamodo_object.filetimes

[974422800.0, 974505600.0]